# 1 Setting Up

## 1.0 Importing packages

In [1]:
import yfinance as yf
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd
from numpy import sqrt
import numpy as np
from math import inf
import cpi
import seaborn as sns
from datetime import datetime, timedelta
from joblib import Parallel, delayed
import time
from itertools import combinations
import json
import time
from multiprocessing import Pool, cpu_count
from tqdm import tqdm
import plotly.io as pio

## 1.1 Defining Functions

In [2]:

def read_csv(file_path):
    """
    Reads a CSV file and returns a DataFrame.
    
    Args:
        file_path (str): The path to the CSV file.
    
    Returns:
        DataFrame: A DataFrame containing the data from the CSV file.
    """
    try:
        df = pd.read_csv(file_path, parse_dates=True, index_col=0)
        return df
    except FileNotFoundError:
        print(f"File not found: {file_path}")
        return None
    except Exception as e:
        print(f"Error reading file {file_path}: {e}")
        return None

def write_csv(file_path, data_frame):
    """
    Writes a DataFrame to a CSV file.
    
    Args:
        file_path (str): The path to the CSV file.
        data_frame (DataFrame): The DataFrame to be written to the CSV file.
    """
    try:
        data_frame.to_csv(file_path)
        print(f"Data successfully written to {file_path}")
    except Exception as e:
        print(f"Error writing to file {file_path}: {e}")
        return None
    
#Get stock/comodity/... data form Yahoo Finance
def get_price_data(ticker_name, start_date, end_date):
    """
    Fetches historical data for a given ticker from Yahoo Finance.
    
    Args:
        ticker_name (str): The ticker symbol of the stock.
        start_date (str): The start date for the historical data in 'YYYY-MM-DD' format.
        end_date (str): The end date for the historical data in 'YYYY-MM-DD' format.
    
    Returns:
        DataFrame: A DataFrame containing the historical stock data.
    """
        
    try:
    
        ticker = yf.Ticker(ticker_name)
        
    except Exception as e:
        print(f"Error fetching ticker {ticker_name}: {e}")
        return None

    to_return = ticker.history(start=start_date, end=end_date)
    if to_return.empty:
        print(f"Ticker {ticker_name} is empty or not found.")
        return None

    return to_return



def get_PE_ratio(ticker_name, date):
    # it only gathers PE ( earnings  ) from 5 year prior to the current date
    """
    Fetches earnings data for a given ticker from Yahoo Finance.
    Args:
        ticker_name (str): The ticker symbol of the stock.
        start_date (str): The start date for the historical data in 'YYYY-MM-DD' format.
        end_date (str): The end date for the historical data in 'YYYY-MM-DD' format.
    
    Returns:
        DataFrame: A DataFrame containing the earnings data.
    """
    try:
    
        ticker = yf.Ticker(ticker_name)
        
    except Exception as e:
        print(f"Error fetching ticker {ticker_name}: {e}")
        raise ValueError(f"Ticker {ticker_name} is not in the list of valid tickers.")

    date = pd.to_datetime(date).normalize()

    stmt = ticker.income_stmt
    net_income = stmt.loc['Net Income']
    
    # how do i see if the date's year is newer or equal to the net_income's oldest year?

    if date.year < net_income.index[0].year:
        print(f"Date {date} is too old for {ticker_name}.")
        return None 
    else:
        # get the closest net income to the date

        time_deltas = net_income.index - date

        closest_date = net_income.index[np.abs(time_deltas).argmin()]
        net_income = net_income.loc[closest_date]
    
    if net_income is None or net_income == 0:
        print(f"No net income data available for {ticker_name} on {closest_date}.")
        return None


    # calculating Earnings per Share (EPS) at the chosen date
    try:
        shares_diluted = stmt.loc['Diluted Average Shares']

        # find the closest date to closest_date to get the shares oustanding
        time_deltas = shares_diluted.index - closest_date
        closest_shares_date = shares_diluted.index[np.abs(time_deltas).argmin()]
        
        shares_diluted = shares_diluted.loc[closest_shares_date]
        eps = net_income / shares_diluted

    except Exception as e:
        print(f"Error calculating EPS for {ticker_name} on {closest_date}: {e}")
        return None

    # Now that i Have EPS, i can calculate the P/E ratio

    date_share_price = ticker.history(start=closest_date, end=closest_date + timedelta(days=10))['Close'].iloc[0]

    return date_share_price / eps



# Plot a Scatter Graph 
def plot_scatter(x_values, y_values, x_label, y_label, title):

    "create a pd data_frame with x_values and y_values"
    pd_data_frame = pd.DataFrame({x_label: x_values, y_label: y_values})
    fig = px.scatter(pd_data_frame, x=x_label, y= y_label , title= title)
    return fig


def generate_cpi_csv(cpi_file_path):
    cpi.update()

    "load cpi values to csv, to acelerate the process of future calculations"
    data_frame = pd.DataFrame({'Year': list(range(1913, datetime.now().year + 1))})

    for year in range (1913, datetime.now().year):
        data_frame.loc[data_frame['Year'] == year, 'CPI'] = cpi.get(year)

        if year % 2 == 0:
            print(f"Year {year} CPI value: {data_frame.loc[data_frame['Year'] == year, 'CPI'].values[0]}")
            print(f"{(year - 1913)/125}")

    # Save the CPI values to a CSV file
    data_frame.to_csv('cpi_values.csv', index=False)

    data_frame = 0
    return 1
    
def get_closest_avaible_date(stock_df, date):
    """
    Finds the closest available date in the stock DataFrame to the given date.
    Args:
        stock_df (DataFrame): A DataFrame containing stock prices with a DateTime index.
        date (datetime): The date for which to find the closest available date.
    
    Returns:
        datetime: The closest available date in the stock DataFrame.
    """
    date = pd.to_datetime(date).normalize()
    # make the date tz ( timezone ) naive

    if hasattr(date, 'tz_localize'):
        date = date.tz_localize(None)

    available_dates = stock_df.index
    # make avaible_date tz naive

    if not isinstance(available_dates, pd.DatetimeIndex):
        available_dates = pd.to_datetime(available_dates)
    if isinstance(available_dates, pd.DatetimeIndex):
        available_dates = available_dates.tz_localize(None)

    closest_date = available_dates[np.abs(available_dates - date).argmin()]

    if closest_date is None:
        return None
    
    closest_date = pd.to_datetime(closest_date).normalize().strftime('%Y-%m-%d')
    return closest_date

# Load Cpi Data
def get_cpi_data(cpi_file_path):
    """
    Loads CPI data from a CSV file and returns it as a DataFrame.
    
    Args:
        cpi_file_path (str): The path to the CSV file containing CPI data.
    
    Returns:
        DataFrame: A DataFrame containing the CPI data with 'year' and 'CPI' columns.
    """

    try:
        cpi_df = pd.read_csv(cpi_file_path)
        cpi_df.columns = ['year', 'CPI']
        return cpi_df
    
    except FileNotFoundError:
        print(f"CPI file not found at {cpi_file_path}. Generating new CPI data...")
        generate_cpi_csv(cpi_file_path)
        cpi_df = pd.read_csv(cpi_file_path)
        cpi_df.columns = ['year', 'CPI']
        return cpi_df


# Get Present Value for a given year based on CPI data
def get_present_value(value_on_other_year, target_year, other_year, cpi_df):
    """
    Calculates the present value of a given amount based on CPI data.
    
    Args:
        value (float): The amount to be adjusted for inflation.
        target_year (int): The year to which the value should be adjusted.
        other_year (int): The year from which the value is being adjusted.
        cpi_df (DataFrame): A DataFrame containing CPI data with 'year' and 'cpi' columns.
    
    Returns:
        float: The present value adjusted for inflation.
    """
    cpi_target = cpi_df[cpi_df['year'] == target_year]['CPI'].values[0]
    cpi_other = cpi_df[cpi_df['year'] == other_year]['CPI'].values[0]
    
    return value_on_other_year * (cpi_target / cpi_other)

def calculate_present_value_for_row(row, target_year, cpi_df):
    # row.name holds the index label (the date)
    return get_present_value(row['Close'], target_year, row.name.year, cpi_df)

def get_series_present_value(stock_df, target_year = 1960, cpi_df = get_cpi_data('cpi_values.csv')):
    '''
    inflation_corrected_prices = []
    size = len(stock_df)

    for index in range(len(stock_df)):
        date_from_index = stock_df.index[index]
        inflation_corrected_prices.append(get_present_value(stock_df['Close'].iloc[index], target_year, date_from_index.year, cpi_df))

        if index % 1000 == 0:
            print(f"Processed {index} out of {size}: {index*100/size:.2f}%    ", end='\r')
    '''
    #trying vectorized aproach
    inflation_corrected_prices = stock_df.apply(lambda row: calculate_present_value_for_row(row, target_year, cpi_df), axis=1)

    #creating a new dataframe with the original x values, but with the new y values ( inflation corrected prices )

    inflation_corrected_df = pd.DataFrame({
        'Close': inflation_corrected_prices
    }, index = stock_df.index)

    return inflation_corrected_df


def price_variation(stock, start_date, end_date): #example of start date: 2020-01-01
    future_value = stock.loc[end_date, 'Close']
    past_value = stock.loc[start_date, 'Close']
    variation = (future_value - past_value) / past_value
    return variation


def get_variation_series(stock_df: pd.DataFrame, start_date: str, end_date: str, period_calculation='weekly'):

    """
    Calculates the periodic percentage variations of stock prices using an optimized
    and accurate pandas workflow.
    
    Args:
        stock_df (DataFrame): A DataFrame containing stock prices with a 'Close' column.
        start_date (str): The start date for the variation calculation.
        end_date (str): The end date for the variation calculation.
        period_calculation (str): The period ('daily', 'weekly', 'monthly', 'yearly').
    
    Returns:
        DataFrame: A DataFrame with the percentage variation of stock prices.
    """
    if period_calculation not in ['weekly', 'monthly', 'yearly', 'daily']:
        raise ValueError("period_calculation must be one of 'weekly', 'monthly', 'yearly', or 'daily'.")

    # 1. --- DATA PREPARATION ---
    # Ensure the DataFrame and dates are clean and timezone-naive
    
    # Work with a copy to avoid side effects
    df = stock_df.copy()
    
    # Make sure the index is a proper DatetimeIndex and is timezone-naive
    df.index = pd.to_datetime(df.index)
    if df.index.tz is not None:
        df.index = df.index.tz_localize(None)

    # Convert start/end dates and make them naive
    start_ts = pd.to_datetime(start_date).normalize().tz_localize(None)
    end_ts = pd.to_datetime(end_date).normalize().tz_localize(None)
    
    # Slice the DataFrame to the desired date range
    df_in_range = df.loc[start_ts:end_ts]
    
    if df_in_range.empty:
        return pd.DataFrame({'Variation': []}) # Return empty if no data in range

    # 2. --- RESAMPLE TO THE DESIRED PERIOD ---
    
    if period_calculation == 'daily':
        # For daily, we can use the data as is
        periodic_df = df_in_range
    else:
        # For other periods, resample the data.
        freq_map = {'weekly': 'W', 'monthly': 'ME', 'yearly': 'YE'}
        
        # .resample() groups the data by the specified frequency.
        # .last() takes the last data point in each period (e.g., the closing price of the week).
        periodic_df = df_in_range.resample(freq_map[period_calculation]).last()
    
    # 3. --- CALCULATE PERCENTAGE CHANGE ---
    # .pct_change() is the highly optimized, vectorized function for this exact task.
    variation_series = periodic_df['Close'].pct_change()
    
    # 4. --- RETURN THE FINAL DATAFRAME ---
    final_df = pd.DataFrame({'Variation': variation_series})
    
    # The first value will be NaN (since there's no previous period to compare to).
    # It's good practice to remove it.
    final_df.dropna(inplace=True)
    
    return final_df

def calc_beta(variation_series_1: pd.DataFrame, variation_series_2: pd.DataFrame):
    # How stock 1 relates to stock 2, beta = 1 directly related, beta = 0 not related, beta = -1 inversely related
    # i will create a new Data_frame, with the same index labels as stock1, but with the columns "var_stock1" and "var_stock2", with variation week by week maybe ?
    # THIS IS THE SISTEMATIC RISK, the risk that cannot be diversified away, the risk that is related to the market as a whole

    beta = variation_series_1['Variation'].cov(variation_series_2['Variation']) / variation_series_2['Variation'].var()
    intercept = variation_series_2['Variation'].mean() - beta * variation_series_1['Variation'].mean()
    return (beta, intercept)


def calc_standard_deviation(stock_series: pd.DataFrame, start_date, end_date):
    # TOTAL RISK
    """
    Calculates the standard deviation of the variation series between two dates.
    
    Args:
        variation_series (DataFrame): A DataFrame containing the variation series with a 'Variation' column.
        start_date (datetime.date): The start date for the calculation.
        end_date (datetime.date): The end date for the calculation.
    
    Returns:
        float: The standard deviation of the variation series between the two dates.
    """

    #Convert to datetime if string
    if type(start_date) is str:
        start_date = pd.to_datetime(start_date)
    if type(end_date) is str:
        end_date = pd.to_datetime(end_date)
    start_date = start_date.normalize()
    end_date = end_date.normalize()

    filtered_series = stock_series[(stock_series.index >= start_date) & (stock_series.index <= end_date)]
    return filtered_series.std()['Variation']



## 1.2 Defining Classes

In [3]:
# Calculate the Sharpe Ratio: excess return per unit of risk. the higher, the better
# The Sharpe Ratio is a measure of risk-adjusted return, indicating how much excess return an investment generates for each unit of risk taken.
# It can be Used To Calculate how weel diversified my portfolio is, and how much risk i am taking for the return i am getting


class Sharpe_Ratio_Calculator:
    def __init__(self, proxy_stock_ETF = get_price_data("^IRX", "1961-06-30", datetime.now().strftime('%Y-%m-%d'))):
        """
        Initializes the Sharpe Ratio calculator with a proxy stock ETF ( Risk Free Rate ).
        """
        # proxy_stock_ETF = get_price_data("BIL", start_date, end_date)  use this proxy as proxy_stock_ETF - select the largest time delta possible
        self.proxy_stock_ETF = proxy_stock_ETF
        self.proxy_stock_ETF.index = self.proxy_stock_ETF.index.tz_localize(None)  # Remove timezone information from index

    def calculate(self, variation_series: pd.DataFrame, start_date, end_date, period_calculation='weekly'):
        """
        Calculates the Sharpe Ratio for a given variation series.
        
        Args:
            variation_series (DataFrame): A DataFrame containing the variation series with a 'Variation' column.
            start_date (str or datetime): The start date for the calculation in 'YYYY-MM-DD' format or as a datetime object.
            end_date (str or datetime): The end date for the calculation in 'YYYY-MM-DD' format or as a datetime object.
            period_calculation (str): The period for which the Sharpe Ratio is calculated ('weekly', 'monthly', 'yearly', or 'daily').
        
        Returns:
            float: The Sharpe Ratio of the variation series.
        """
        # The period_calculation should be the same as the one used in get_variation_series
        # proxy_stock_ETF = get_price_data("BIL", start_date, end_date)  use this proxy as proxy_stock_ETF
        """
        Calculates the Sharpe Ratio for a given variation series.
        """
        if period_calculation not in ['weekly', 'monthly', 'yearly', 'daily']:
            raise ValueError("period_calculation must be one of 'weekly', 'monthly', 'yearly', or 'daily'.")

        if period_calculation == 'daily':
            anual_periods = 252  # Approximation for daily trading days in a year

        if period_calculation == 'weekly':
            anual_periods = 52  # Approximation for weeks in a year
            
        elif period_calculation == 'monthly':
            anual_periods = 12  # Months in a year

        elif period_calculation == 'yearly':
            anual_periods = 1  # For yearly calculations, we consider it as one period


        if type(start_date) is str:
            start_date = pd.to_datetime(start_date)
        if type(end_date) is str:
            end_date = pd.to_datetime(end_date)
        start_date = start_date.normalize()
        end_date = end_date.normalize()

        # Calculating the risk_free_rate, with the same period_calculation, and get the number of periods in a year
        
        #proxy_stock_ETF = get_price_data("BIL", start_date, end_date)  


        variation_series.index = variation_series.index.tz_localize(None)  # Remove timezone information from index
        
        filtered_series = self.proxy_stock_ETF[(self.proxy_stock_ETF.index >= start_date) & (self.proxy_stock_ETF.index <= end_date)]
        mean_annual_risk_free_rate = filtered_series['Close'].mean() / 100.0

        risk_free_periodic_rate = mean_annual_risk_free_rate / anual_periods
        # Retuning the anualized Sharpe Ratio

        filtered_portfolio_series = variation_series[(variation_series.index >= start_date) & (variation_series.index <= end_date)]
        portfolio_periodic_returns = filtered_portfolio_series['Variation']
        avg_excess_return = portfolio_periodic_returns.mean() - risk_free_periodic_rate

        portfolio_volatility = portfolio_periodic_returns.std()
        sharpe_ratio = (avg_excess_return / portfolio_volatility) * sqrt(anual_periods)
        return sharpe_ratio
        
    

# Class Portfolio:
# has the stocks the users owns
# the get_risk for the whole portfolio
# The Plot_earings x risk graph, and maybe write the data to a csv file
# i need to implement something to counter the Stock Split if it happens - it does not

class Portfolio:
    def __init__(self, id: int, money: float):
        """
        Initializes the Portfolio with a name and an empty list of stocks.
        
        Args:
            name (str): The name of the portfolio.
        """
        self.initial_money = money
        self.bank_account = money
        self.id = id
        self.stocks_tickers = []
        self.stocks = {}
        self.stocks_total_price_history_df = pd.DataFrame(columns=['Close']) # index is dates, "Close" is the Total Price in Portfolio
        self.variating_portfolio_value_series = None
        self.variating_portfolio_risk = None

        #here "stocks" can also be ETFs
        # I will not have to worry about Stock Splits or Dividends altering the value, because yfinance already takes care of that when fetching the data
        '''
         self.stocks = {
            stock_ticker: [ -- this is a list because i can buy multiple times the same stock

                {
                    'quantity': quantity ( int ),
                    'purchase_unit_price': purchase_unit_price,
                    'purchase_date': purchase_date,
                    'earned_dividends': earned_dividends ( float ) ( 0 ) for ETFs and stocks that do not pay dividends,
                    'type': 'stock', 'ETFs (Market Indices, Commodities, Currencies, Crypto, )', Mutual_funds, bond

                }
            ]
         }
        '''

    def owned_share(self, ticker):
        if ticker in self.stocks_tickers and self.owned_share_quantity(ticker) > 0:
            return True
        return False

    def owned_share_quantity(self, stock_ticker):
        """
        Returns the total quantity of shares owned for a given stock ticker.
        
        Args:
            stock_ticker (str): The ticker symbol of the stock.
        
        Returns:
            int: The total quantity of shares owned for the given stock ticker.
        """
        if stock_ticker not in self.stocks_tickers:
            return 0
        
        total_quantity = sum(item['quantity'] for item in self.stocks[stock_ticker])
        return total_quantity
    
    def buy_stock(self, stock_ticker, money_spent, purchase_date, stock_type):
        """
        Adds a stock to the portfolio.
        
        Args:
            stock (Stock): The stock to be added to the portfolio.
        """
        # Getting number of shares bought

        try:

            purchase_date = pd.to_datetime(purchase_date).normalize()
            # make the purchase_date tz naive
            purchase_date = purchase_date.tz_localize(None)
            price_data = get_price_data(stock_ticker, purchase_date - timedelta(days=5), purchase_date + timedelta(days=5))

            if price_data is None:
                print(f"No available data for {stock_ticker} on {purchase_date}.")
                return None
        
            date = get_closest_avaible_date(price_data, purchase_date)

            if date is None:
                print(f"No available data for {stock_ticker} on {purchase_date}.")
                return None
        
        
        except Exception as e:
            print(f"Error fetching price data for {stock_ticker} on {purchase_date}: {e}")
            return None
        
        purchase_unit_price = price_data.loc[date, 'Close']
        quantity = money_spent // purchase_unit_price
        
        self.bank_account -= quantity * purchase_unit_price

        if stock_ticker not in self.stocks_tickers:
            self.stocks_tickers.append(stock_ticker)
            self.stocks[stock_ticker] = []
        
        self.stocks[stock_ticker].append({
            'quantity': quantity,
            'purchase_unit_price': purchase_unit_price,
            'purchase_date': date,
            'earned_dividends': 0.0,  # Initialize earned dividends to 0
            'type': stock_type  # e.g., 'stock', 'ETF', etc.
        })

        #returns the quantity of shares bought
        return quantity
        
    
    def sell_stock(self, stock_ticker, quantity, date, all = False):
        """
        Sells a stock from the portfolio.
        
        Args:
            stock_ticker (str): The ticker symbol of the stock to be sold.
            quantity (int): The quantity of the stock to be sold.
        """
        date = pd.to_datetime(date).normalize()
        # make the date tz naive
        date = date.tz_localize(None)

        if stock_ticker not in self.stocks_tickers:
            print(f"Stock {stock_ticker} not found in portfolio.")
            return None
        
        #getting selling price
        price_data = get_price_data(stock_ticker, date - timedelta(days=3), date + timedelta(days=3))
        closest_date = get_closest_avaible_date(price_data, date)

        if closest_date is None:
            print(f"No available data for {stock_ticker} on {date}.")
            return None

        stock = self.stocks[stock_ticker]

        if stock[0]['type'] == 'bond':
            for item in stock:
                quantity = item['quantity']

                buying_date = pd.to_datetime(item['purchase_date']).normalize()
                # make the buying_date tz naive
                buying_date = buying_date.tz_localize(None)
                weeks_passed = (date - buying_date).days // 7
                anual_yield_data = item['purchase_unit_price'] /100
                weekly_yield_data = (1 + anual_yield_data)**(1/52) - 1
                selling_price = item['purchase_unit_price'] * (1 + weekly_yield_data)**weeks_passed

                sale_price = quantity * selling_price
                if sale_price <= 0:
                    sale_price = 0.0

        else:
            selling_price = price_data.loc[closest_date, 'Close']

            sell_all = all
            
            if quantity > sum(item['quantity'] for item in stock):

                print(f"trying to sell {quantity}, but you have {sum(item['quantity'] for item in stock)}")
                print(f"Not enough shares of {stock_ticker} to sell, selling all you have.")
                quantity = sum(item['quantity'] for item in stock)
                sell_all = True
        
            # Calculate the total sale price
            sale_price = quantity * selling_price
            if sale_price <= 0:
                sale_price = 0.0
            
            # Remove the sold stock from the portfolio
            if sell_all:
                self.stocks_tickers.remove(stock_ticker)
                del self.stocks[stock_ticker]

            else:
                # Remove the sold quantity from the stock
                for item in stock:
                    if item['quantity'] >= quantity:
                        item['quantity'] -= quantity
                        if item['quantity'] == 0:
                            stock.remove(item)
                        break
                    else:
                        quantity -= item['quantity']
                        stock.remove(item)

        self.bank_account += sale_price
        return 1
    
    def portfolio_value(self, date):
        # not going to implement dividends now
        """
        Calculates the total value of the portfolio by summing the values of all stocks.
        
        Returns:
            float: The total value of the portfolio.
        """

        #make the print replace the previous one , for better visualization in the terminal
        print(f"calculating portfolio value for {date}...", end='\r')

        

        date = pd.to_datetime(date).normalize()
        # make the date tz naive
        date = date.tz_localize(None)

        value = 0.0
        for ticker in self.stocks_tickers:
            
            if date < pd.to_datetime(self.stocks[ticker][0]['purchase_date']).normalize():
                continue

            quantity = 0
            if ticker not in self.stocks:
                continue
            
            # get the date ticker value

            try:
                price_data = get_price_data(ticker, date - timedelta(days=3), date + timedelta(days=3))
                closest_date = get_closest_avaible_date(price_data, date)
                
                if closest_date is None:
                    print(f"No available data for {ticker} on {date}.")
                    continue

                current_price = price_data.loc[closest_date, 'Close']

                ticker_buys = self.stocks[ticker]
                stock = True

                for buy in ticker_buys:

                    if buy['type'] == 'bond':

                        stock = False
                        # i need to get every year yield since bought
                        # and calculate the value of the bond at the current date
                        purchase_date = pd.to_datetime(buy['purchase_date']).normalize()
                        # make the purchase_date tz naive
                        purchase_date = purchase_date.tz_localize(None)
                        anual_yield_data = buy['purchase_unit_price'] /100
                        weekly_yield_data = (1 + anual_yield_data)**(1/52) - 1

                        # calculating how many weeks passed since the bond aquirement
                        weeks_passed = (pd.to_datetime(date) - purchase_date).days // 7

                        # calculating the current value of the bond
                        current_bond_value = buy['quantity']*buy['purchase_unit_price'] * (1 + weekly_yield_data)**weeks_passed
                        value += current_bond_value
                        
                    else:
                        quantity += buy['quantity']

                if stock:
                    value += quantity * current_price

            except Exception as e:
                print(f"Error fetching price data for {ticker} on {date}: {e}")
                

        return value


    def calculate_time_series_portfolio_value(self, start_date, end_date, period_calculation='weekly'):
        '''
            1) deletes the data in self.stocks_total_price_history_df
            2) calculates the total value of the portfolio for each date in the range from start_date to end_date, with 'date' as its index
            3) stores the results in self.stocks_total_price_history_df
        '''
        start_date = pd.to_datetime(start_date).normalize()
        end_date = pd.to_datetime(end_date).normalize()
        # make the start_date and end_date tz naive
        start_date = start_date.tz_localize(None)
        end_date = end_date.tz_localize(None)

        #frequency_calculation ( delta )

        if period_calculation not in ['weekly', 'monthly', 'yearly', 'daily']:
            raise ValueError("period_calculation must be one of 'weekly', 'monthly', 'yearly', or 'daily'.")
        if period_calculation == 'daily':
            delta = timedelta(days=1)
        elif period_calculation == 'weekly':
            delta = timedelta(weeks=1)
        elif period_calculation == 'monthly':
            delta = timedelta(days=30)
        elif period_calculation == 'yearly':
            delta = timedelta(days=365)

        freq_map = {
            'daily': 'D',
            'weekly': 'W',  # 'W-SUN' for Sunday, 'W-MON' for Monday, etc. 'W' defaults to Sunday.
            'monthly': 'ME', # 'ME' for Month End frequency. Use 'MS' for Month Start.
            'yearly': 'YE',  # 'YE' for Year End frequency. Use 'YS' for Year Start.
        }

        if period_calculation not in freq_map:
            raise ValueError("period_calculation must be one of 'weekly', 'monthly', 'yearly', or 'daily'.")
        
        #indexes_list = pd.date_range(start=start_date, end=end_date, freq=freq_map[period_calculation]).to_list()

        #if not indexes_list:
            #self.stocks_total_price_history_df = pd.DataFrame({'Close': []})
            #return 1

        full_date_range = pd.date_range(start=start_date - timedelta(days=5), end=end_date, freq="D")

        if not self.stocks:
            self.stocks_total_price_history_df = pd.DataFrame(index=full_date_range, columns=['Close']).fillna(0)
            return 1
        
        list_of_records = [
            {'ticker': ticker, **transaction}
            for ticker, transaction_list in self.stocks.items()
            for transaction in transaction_list
        ]

        transactions_df = pd.DataFrame(list_of_records)
        transactions_df['purchase_date'] = pd.to_datetime(transactions_df['purchase_date']).dt.tz_localize(None).dt.normalize()

        all_prices_df = pd.DataFrame(index=full_date_range)

        for ticker in self.stocks_tickers:
            price_series = get_price_data(ticker, start_date, end_date)["Close"]

            if not price_series.empty:
                price_series = price_series.tz_localize(None)
                # Reindex and forward-fill missing values (weekends, holidays)
                all_prices_df[ticker] = price_series.reindex(full_date_range, method='ffill')

        all_prices_df.bfill(inplace=True)  # Backfill to fill any remaining NaNs at the end of the date range
        #all_prices_df.fillna(0, inplace=True) # Fill any remaining NaNs with 0

        #Vectorizing Calculations

        stock_transactions = transactions_df[transactions_df['type'] != 'bond'].copy()
        bond_transactions = transactions_df[transactions_df['type'] == 'bond'].copy()
        
        if not stock_transactions.empty:
            # Sum quantities for each ticker on each purchase day
            daily_stock_purchases = stock_transactions.groupby(['purchase_date', 'ticker'])['quantity'].sum().unstack(fill_value=0)
            # Reindex to our full date range and take the cumulative sum to get holdings over time
            daily_stock_quantities = daily_stock_purchases.reindex(full_date_range, fill_value=0).cumsum()
            

        # Multiply the daily quantities matrix by the daily prices matrix element-wise
        daily_stock_values = daily_stock_quantities * all_prices_df[daily_stock_quantities.columns]
        total_daily_stock_value = daily_stock_values.sum(axis=1)
        
        #Calculating Bonds:

        total_daily_bond_value = pd.Series(0, index=full_date_range)

        if not bond_transactions.empty:
        # This part is harder to fully vectorize, but we can vectorize the loop over transactions
            daily_bond_values_list = []
            for _, bond in bond_transactions.iterrows():
                purchase_date = bond['purchase_date']
                
                # Create a Series of days passed for the entire date range
                days_passed = (full_date_range - purchase_date).days
                weeks_passed = np.floor(days_passed / 7).astype(int)
                
                # Calculate yield
                annual_yield = bond['purchase_unit_price'] / 100.0
                weekly_yield = (1 + annual_yield) ** (1/52) - 1
                
                # Calculate the value over time for this single bond
                initial_value = bond['quantity'] * bond['purchase_unit_price']
                bond_value_array = initial_value * (1 + weekly_yield) ** weeks_passed

                bond_value_series = pd.Series(bond_value_array, index=full_date_range)

                # Mask the values for dates before the purchase'
                condition_to_keep = full_date_range >= purchase_date
                masked_bond_value_series = bond_value_series.where(condition_to_keep, 0)

            
                daily_bond_values_list.append(masked_bond_value_series)
                
            # Sum the value series of all individual bonds to get the total
            if daily_bond_values_list:
                total_daily_bond_value = pd.concat(daily_bond_values_list, axis=1).sum(axis=1)
        
        
         # Combine the total stock and bond values
        total_portfolio_value = total_daily_stock_value + total_daily_bond_value
        
        # Store the final result in the required format
        self.stocks_total_price_history_df = pd.DataFrame({'Close': total_portfolio_value})

        # The `period_calculation` logic can now be applied AFTER the daily calculation
        if period_calculation != 'daily':
            freq_map = {'weekly': 'W', 'monthly': 'ME', 'yearly': 'YE'}
            # Resample the daily data to the desired frequency
            self.stocks_total_price_history_df = self.stocks_total_price_history_df.resample(freq_map[period_calculation]).last()
        return 1        

    def get_time_series_portfolio_value(self):

        if self.stocks_total_price_history_df.empty:
            print("No time series portfolio value calculated yet. Please run calculate_time_series_portfolio_value() first.")
            return None
        return self.stocks_total_price_history_df

    def calculate_variating_portfolio_value(self, start_date, end_date, period_calculation='weekly'):

        if self.stocks_total_price_history_df.empty or pd.to_datetime(start_date).normalize() < self.stocks_total_price_history_df.index[0] or pd.to_datetime(end_date).normalize() > self.stocks_total_price_history_df.index[-1]:
            self.calculate_time_series_portfolio_value(start_date, end_date, period_calculation)
        
        if period_calculation not in ['weekly', 'monthly', 'yearly', 'daily']:
            raise ValueError("period_calculation must be one of 'weekly', 'monthly', 'yearly', or 'daily'.")
        
        self.variating_portfolio_value_series = get_variation_series(self.stocks_total_price_history_df, start_date, end_date, period_calculation)

        return self.variating_portfolio_value_series
    
    def get_variating_portfolio_value(self, start_date, end_date, period_calculation='weekly'):
        """
        Returns the variating portfolio value series.
        
        Returns:
            DataFrame: The variating portfolio value series.
        """
        if self.variating_portfolio_value_series is None:
            print(f"No variating portfolio value calculated yet. calculating for start_date: {start_date}, end_date: {end_date},  period_calculation: {period_calculation}.")
            self.calculate_variating_portfolio_value(start_date, end_date, period_calculation)
            return self.variating_portfolio_value_series
        
        # checking if start_date and end_date are in the variating portfolio value series or the delta_calculation is smaller than the variting dates of the series
        if period_calculation not in ['weekly', 'monthly', 'yearly', 'daily']:
            raise ValueError("period_calculation must be one of 'weekly', 'monthly', 'yearly', or 'daily'.")
        if period_calculation == 'daily':
            delta = timedelta(days=1)
        elif period_calculation == 'weekly':
            delta = timedelta(weeks=1)
        elif period_calculation == 'monthly':
            delta = timedelta(days=30)
        elif period_calculation == 'yearly':
            delta = timedelta(days=365)
        

        if self.variating_portfolio_value_series.index[0] > pd.to_datetime(start_date).normalize() or self.variating_portfolio_value_series.index[-1] < pd.to_datetime(end_date).normalize() or self.variating_portfolio_value_series.index[1] - self.variating_portfolio_value_series.index[0] >= delta:
            #print("Portfolio Variating Series not in the data_range, Calculating variating portfolio value series...")
            self.calculate_variating_portfolio_value(start_date, end_date, period_calculation)
        
        return self.variating_portfolio_value_series


    def calculate_portfolio_risk(self, start_date, end_date, period_calculation='weekly'):
        """
        Calculates the risk of the portfolio based on the variating portfolio value series.
        
        Args:
            start_date (str): The start date for the risk calculation in 'YYYY-MM-DD' format.
            end_date (str): The end date for the risk calculation in 'YYYY-MM-DD' format.
            period_calculation (str): The period for which the risk is calculated ('weekly', 'monthly', 'yearly', or 'daily').
        
        Returns:
            float: The standard deviation of the variating portfolio value series.
        """

        if period_calculation not in ['weekly', 'monthly', 'yearly', 'daily']:
            raise ValueError("period_calculation must be one of 'weekly', 'monthly', 'yearly', or 'daily'.")
        if period_calculation == 'daily':
            delta = timedelta(days=1)
        elif period_calculation == 'weekly':
            delta = timedelta(weeks=1)
        elif period_calculation == 'monthly':
            delta = timedelta(days=30)
        elif period_calculation == 'yearly':
            delta = timedelta(days=365)


        if self.variating_portfolio_value_series is None:
            #print("Portfolio Variating Series not calculated, Calculating variating portfolio value series...")
            self.calculate_variating_portfolio_value(start_date, end_date, period_calculation)

        else:
            if self.variating_portfolio_value_series.index[0] > pd.to_datetime(start_date) or self.variating_portfolio_value_series.index[-1] < pd.to_datetime(end_date):
                #print("Portfolio Variating Series not in the data_range, Calculating variating portfolio value series...")
                self.calculate_variating_portfolio_value(start_date, end_date, period_calculation)
            
        
        return calc_standard_deviation(self.variating_portfolio_value_series, start_date, end_date)
        

    def calculate_variating_portfolio_risk(self, start_date, end_date, period_calculation, datapoints_period_calculation='weekly'):

        '''
        Get risk from T0 to T0 + period_calculation

        '''



        if datapoints_period_calculation not in ['weekly', 'monthly', 'yearly', 'daily']:
            raise ValueError("period_calculation must be one of 'weekly', 'monthly', 'yearly', or 'daily'.")
        if datapoints_period_calculation == 'daily':
            data_delta = timedelta(days=1)
        elif datapoints_period_calculation == 'weekly':
            data_delta = timedelta(weeks=1)
        elif datapoints_period_calculation == 'monthly':
            data_delta = timedelta(days=30)
        elif datapoints_period_calculation == 'yearly':
            data_delta = timedelta(days=365)
        
        if period_calculation not in ['weekly', 'monthly', 'yearly', 'daily']:
            raise ValueError("period_calculation must be one of 'weekly', 'monthly', 'yearly', or 'daily'.")
        if period_calculation == 'daily':
            delta = timedelta(days=1)
        elif period_calculation == 'weekly':
            delta = timedelta(weeks=1)
        elif period_calculation == 'monthly':
            delta = timedelta(days=30)
        elif period_calculation == 'yearly':
            delta = timedelta(days=365)

        if delta <= data_delta:
            raise ValueError("period_calculation must be greater than datapoints_period_calculation.")
        
        self.calculate_portfolio_risk(start_date, end_date, datapoints_period_calculation)


        if self.variating_portfolio_value_series.index[1] - self.variating_portfolio_value_series.index[0] > data_delta:
            #print("Portfolio Variating Series not in the optimal_period")
            self.calculate_variating_portfolio_value(start_date, end_date, datapoints_period_calculation)
        
        start_date_datetime = pd.to_datetime(start_date).normalize()
        end_date_datetime = pd.to_datetime(end_date).normalize()
        # make the start_date and end_date tz naive
        start_date_datetime = start_date_datetime.tz_localize(None)
        end_date_datetime = end_date_datetime.tz_localize(None)

        #frequency_calculation ( delta )
        
        risks = []
        daterange = pd.date_range(start_date_datetime + delta, end_date_datetime, freq = delta)

        # mudei o period_calculation pra daily aqui
        for date in daterange:
            risks.append(self.calculate_portfolio_risk((date - delta).strftime('%Y-%m-%d'), date.strftime('%Y-%m-%d'), period_calculation = datapoints_period_calculation))

        # creating pd dataframe with risks

        dataframe = pd.DataFrame({"Close": risks}, index= daterange)
        return dataframe



        
        

    def reset(self):
        self.bank_account = self.initial_money
        self.stocks_tickers = []
        self.stocks = {}
        self.stocks_total_price_history_df = pd.DataFrame(columns=['Close'])
        self.variating_portfolio_value_series = None
        self.variating_portfolio_risk = None
        


## 1.3. Loading CPI values to CSV to make faster future-processing

In [ ]:
generate_cpi_csv('cpi_values.csv')

# 2. Testing

## 2.1. Testing of get_price_data, get_PE_ratio, plot_scatter, get_series_present_value

In [21]:

apple= get_price_data('AAPL', '1980-01-01', '2023-11-01')
# get the adjusted price of apple


apple_PE_ratio = get_PE_ratio('AAPL', '2025-03-29')
print(f"AAPL PE ratio on 2023-04-26: {apple_PE_ratio}")

#calcualted in the present_value of 1990
apple_present_value = get_series_present_value(apple, 1990)


fig = plot_scatter(apple.index, apple['Close'], 'Date', 'Close Price', 'AAPL Stock Price Over Time')
fig.show()



AAPL PE ratio on 2023-04-26: 38.12254884739627


In [22]:

# Testing Portfolio Class
portfolio1 = Portfolio(1, 100000.0)
portfolio1.buy_stock('AAPL', 0.56, '1990-04-26', 'stock')
print(portfolio1.stocks)
print(portfolio1.portfolio_value('2023-04-26'))

# testing portfolio_series

portfolio1.calculate_time_series_portfolio_value('1990-04-26', '2023-04-26', 'weekly')



{'AAPL': [{'quantity': 2.0, 'purchase_unit_price': 0.27347511053085327, 'purchase_date': '1990-04-26', 'earned_dividends': 0.0, 'type': 'stock'}]}
323.458251953125folio value for 2023-04-26...


1

In [31]:

portfolio1_weekly_value = portfolio1.get_time_series_portfolio_value()
print(portfolio1_weekly_value)
plot_scatter(portfolio1_weekly_value.index, portfolio1_weekly_value['Close'], 'Date', 'Portfolio Value', 'Portfolio Value Over Time').show()


                 Close
1990-04-22    0.000000
1990-04-29    0.550467
1990-05-06    0.562779
1990-05-13    0.599711
1990-05-20    0.559262
...                ...
2023-04-02  325.710052
2023-04-09  325.235992
2023-04-16  326.322357
2023-04-23  325.947021
2023-04-30  323.478058

[1724 rows x 1 columns]


In [32]:
#calculating series_present_value of apple ( target year = 1990 )
apple_present_value_series = get_series_present_value(apple, 1990)
print("Present Value Calculated")
plot_scatter(apple_present_value_series.index, apple_present_value_series['Close'], 'Date', 'Present Value', 'AAPL Present Value Over Time').show()

Present Value Calculated


In [33]:
#putting everything toghether on the same graph
aapl_close = apple['Close'].rename('AAPL Close')
aapl_present_value = apple_present_value_series['Close'].rename('AAPL Present Value')
portfolio_value = portfolio1_weekly_value['Close'].rename('Portfolio Value')

#make all date indexes tz naive
aapl_close.index = aapl_close.index.tz_localize(None)
aapl_present_value.index = aapl_present_value.index.tz_localize(None)
portfolio_value.index = portfolio_value.index.tz_localize(None)

combined_df = pd.concat([aapl_close, aapl_present_value, portfolio_value], axis=1, join="outer")


combined_fig = px.scatter(combined_df, x=combined_df.index, y=combined_df.columns, title='AAPL Stock Price, Present Value, and Portfolio Value Over Time')
combined_fig.update_layout(xaxis_title='Date', yaxis_title='Value')
combined_fig.show()

## 2.2. Testing of variation_series, calc_beta and calc_standard_deviation

In [29]:
# Portfolio variating series:
portfolio1.calculate_variating_portfolio_value('1990-04-26', '2023-04-26', 'weekly')
portfolio1_variating_series = portfolio1.get_variating_portfolio_value('1990-04-26', '2023-04-26')
print(portfolio1_variating_series)

# Getting S&P 500 variating_series
SEP500_price_data = get_price_data('^GSPC', '1990-04-26', '2023-04-26')
SEP500_variating_series = get_variation_series(SEP500_price_data, '1990-04-26', '2023-04-26', 'weekly')

#Plotting Variaitons
plot_scatter(portfolio1_variating_series.index, portfolio1_variating_series['Variation'], 'Date', 'Portfolio Variation', 'Portfolio Variation Over Time').show()
plot_scatter(SEP500_variating_series.index, SEP500_variating_series['Variation'], 'Date', 'S&P 500 Variation', 'S&P 500 Variation Over Time').show()

# Calculating Beta of Portfolio in relation to S&P 500
beta, intercept = calc_beta(portfolio1_variating_series, SEP500_variating_series)
print(f"Portfolio_x_S&P500 Beta: {beta}, Intercept: {intercept}")

#Plotting both variations as : y: portfolio variation, x: S&P 500 variation
plot_scatter(SEP500_variating_series['Variation'], portfolio1_variating_series['Variation'], 'S&P 500 Variation', 'Portfolio Variation', 'Portfolio Variation vs S&P 500 Variation').show()


fig = px.scatter(x=SEP500_variating_series['Variation'][:-1], y=portfolio1_variating_series['Variation'],
                    labels={'x': 'S&P 500 Variation', 'y': 'Portfolio Variation'},
                    title='Portfolio Variation vs S&P 500 Variation with Regression Line')

# Adding the regression line
x_range = np.linspace(SEP500_variating_series['Variation'].min(), SEP500_variating_series['Variation'].max(), 100)
y_range = beta * x_range + intercept
fig.add_scatter(x=x_range, y=y_range, mode='lines', name='Regression Line', line=dict(color='red'))

fig.show()



            Variation
1990-05-06   0.022366
1990-05-13   0.065624
1990-05-20  -0.067447
1990-05-27   0.009081
1990-06-03   0.018749
...               ...
2023-03-26   0.033871
2023-04-02   0.029017
2023-04-09  -0.001455
2023-04-16   0.003340
2023-04-23  -0.001150

[1721 rows x 1 columns]


Portfolio_x_S&P500 Beta: 1.0702996007730798, Intercept: -0.004013040570665965


In [30]:
# Calculating Standard Deviation
portfolio_risk = calc_standard_deviation(portfolio1_variating_series, '1990-04-26', '2023-04-26')
print(f"Portfolio Risk (Standard Deviation): {portfolio_risk*100} %")
SEP500_risk = calc_standard_deviation(SEP500_variating_series, '1990-04-26', '2023-04-26')
print(f"S&P 500 Risk (Standard Deviation): {SEP500_risk*100} %")

portfolio_risk_via_class = portfolio1.calculate_portfolio_risk('1990-04-26', '2023-04-26')
print(f"Portfolio Risk via Class Method (Standard Deviation): {portfolio_risk_via_class*100} %")

Portfolio Risk (Standard Deviation): 5.695904048613519 %
S&P 500 Risk (Standard Deviation): 2.3390076339317947 %
Portfolio Risk via Class Method (Standard Deviation): 5.695904048613519 %


## 2.3 Filtering csvs on the simulation_files


In [ ]:
def validate(ticker):
    status = get_price_data(ticker, '1913-01-01', '2025-05-01')
    if status is None:
        return False
    return True

def validate_csv(path):
    data = read_csv(path)

    validated = data['ticker'].apply(validate)

    final_df = data[validated]
    final_df = final_df.reset_index(drop=True)
    
    final_df.to_csv(path, index=True)

paths_to_validate = [
    'simulating_files/bonds/tickers.csv',
    'simulating_files/commodities//energy/tickers.csv',
    'simulating_files/commodities//metal/tickers.csv',
    'simulating_files/commodities/grains/tickers.csv',
    'simulating_files/commodities/livestock/tickers.csv',
    'simulating_files/commodities/softs/tickers.csv',
    'simulating_files/crypto/crypto/tickers.csv',
    'simulating_files/forex/forex/tickers.csv',
    'simulating_files/indexes/international_indexes/tickers.csv',
    'simulating_files/indexes/us_indexes/tickers.csv',
    'simulating_files/stocks/communications/tickers.csv',
    'simulating_files/stocks/consumer_discretionary/tickers.csv',
    'simulating_files/stocks/energy/tickers.csv',
    'simulating_files/stocks/financials/tickers.csv',
    'simulating_files/stocks/health_care/tickers.csv',
    'simulating_files/stocks/industrials/tickers.csv',
    'simulating_files/stocks/materials/tickers.csv',
    'simulating_files/stocks/real_estate/tickers.csv',
    'simulating_files/stocks/information_technology/tickers.csv',
]

validate_csv('simulating_files/bonds/ETF/tickers.csv')

for path in paths_to_validate[14:]:
    print(f"Validating {path}...")
    validate_csv(path)




/tmp/ipykernel_4778/921375088.py:18: UserWarning:

Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.



'\nfor path in paths_to_validate[14:]:\n    print(f"Validating {path}...")\n    validate_csv(path)\n\n'

# 3. Simulating 

## 3.1 Company's reactions to markets and Sharpe Ratios

In [80]:
# Markets Proxies:
''' 
Energy	XOM
Industrials	^DJT
Financials	XLF - 1998 , the rest: before 1984
Technology	IBM
Health Care	JNJ
Real Estate	WY
Commodities	^SPGSCI
Communications	T
'''

markets_proxies = {
    #'Energy': 'XOM',
    'Energy': 'XLE',
    #'Industrials': '^DJT',
    'Industrials': 'XLI',
    #'Financials': 'AXP',
    'Financials': 'XLF',
    #'Technology': 'IBM',
    'Technology': 'XLK',
    #'Health Care': 'JNJ',
    'Health Care': 'XLV',
    #'Real Estate': 'WY',
    'Real Estate': 'XLRE',
    #'Commodities': 'XLB',
    'Commodities': 'DBC',
    #'Communications': 'T'
    'Communications': 'XLC'

}

raw_materials_proxies = {
    'materials': '^SPGSCI',
    'chemicals': 'DD'
}

tickers_to_analize = {
    '^GSPC' : 'S&P 500',
    'JPM' : 'JPMorgan Chase',
    'ORCL' : 'Oracle Corporation',
    'MSFT' : 'Microsoft Corporation',
    'T' : 'AT&T',
    'NKE' : 'Nike, Inc.',
    'NFLX' : 'Netflix, Inc.',
    'CL=F' : 'Crude Oil Futures',
    'ESS': 'Essex Property Trust, Inc.',
    'BAC' : 'Bank of America Corporation',
    'XOM' : 'Exxon Mobil Corporation',
    'EBAY' : 'eBay Inc.',
    'TTWO' : 'Take-Two Interactive Software, Inc.',
    'UNH' : 'UnitedHealth Group Incorporated',
    'AAPL' : 'Apple Inc.'
}


#Calculating Sharpe Ratios of the tickers, starting from 1992

earnings_risks_sharpe_ratio = {}

sharpe_ratio_calculator = Sharpe_Ratio_Calculator()

for ticker in tickers_to_analize.keys():

    #calculating earning:
    price_data = get_price_data(ticker, start_date='2002-08-04', end_date='2025-04-04')
    variation_series = get_variation_series(price_data, start_date='2002-08-04', end_date='2025-04-04', period_calculation='weekly')
    # mean anual earnings
    earning = get_variation_series(price_data, start_date='2002-08-04', end_date='2025-04-04', period_calculation='yearly').mean()['Variation']

    #risk
    risk = get_variation_series(price_data, start_date='2002-08-04', end_date='2025-04-04', period_calculation='yearly').std()['Variation']

    #calculating sharpe ratio
    sharpe_ratio = sharpe_ratio_calculator.calculate(variation_series, '2002-08-04', '2025-04-04', period_calculation='weekly')

    earnings_risks_sharpe_ratio[ticker] = {
        'earning': earning,
        'risk': risk,
        'sharpe_ratio': sharpe_ratio
    }

companys_analitics = pd.DataFrame(earnings_risks_sharpe_ratio)
print(companys_analitics)
# save the companys analitics to a json file
companys_analitics.to_json("results/companys_analitics.json")



                 ^GSPC       JPM      ORCL      MSFT         T       NKE  \
earning       0.096321  0.156569  0.149257  0.181759  0.106120  0.148512   
risk          0.167001  0.233273  0.224594  0.276658  0.210128  0.257969   
sharpe_ratio  0.461280  0.492432  0.544995  0.644579  0.421719  0.514220   

                  NFLX      CL=F       ESS       BAC       XOM      EBAY  \
earning       0.641449  0.086106  0.142488  0.093331  0.113198  0.172061   
risk          1.108314  0.332796  0.236339  0.369362  0.261843  0.379098   
sharpe_ratio  0.808041  0.261529  0.506393  0.247135  0.408129  0.455454   

                  TTWO       UNH      AAPL  
earning       0.186194  0.193784  0.464391  
risk          0.393620  0.238762  0.605202  
sharpe_ratio  0.455611  0.588020  1.050719  


In [81]:
#plotting
plot_df = pd.DataFrame.from_dict(earnings_risks_sharpe_ratio, orient='index')

plot_df.reset_index()
plot_df.rename(columns={'index': 'Ticker'})

fig = px.bar(
    plot_df,
    x = plot_df.index,
    y = "sharpe_ratio",
    title = "Sharpe Ratios",
    color=plot_df.index,
    text='sharpe_ratio', 
    labels={'y': 'Sharpe Ratio', 'x': 'Asset Ticker'}
)

fig.update_traces(texttemplate='%{text:.4f}', textposition='outside')
fig.write_image("results/comapnys_sharpe_ratios.png")
fig.show()


plot_df.reset_index()
plot_df_2 = plot_df.rename(columns={'index': 'Ticker'})
plot_df_2['Ticker'] = plot_df_2.index


long_df = pd.melt(
    plot_df_2,
    id_vars=["Ticker"],
    value_vars=["earning", "risk", "sharpe_ratio"],
    var_name="Metric",
    value_name="Value"
)


fig_2 = px.bar(
    long_df,
    x="Ticker",
    y="Value",
    color="Metric",
    title="Earnings, Risks, and Sharpe Ratios",
    barmode="group",
    labels={'Value': 'Value', 'Ticker': 'Asset Ticker', 'Metric': 'Metric Type'}
)

fig_2.write_image("results/companys_analitics.png")
fig_2.show()


In [82]:
#How Each company Reacts to each market
#getting data from the markets:
'''
market_data = {
    'name' : {
        'price_data': data,
        "variation_series": variation_series,
        "ticker": str,
    }
}

'''
market_data = {}

for market_name in markets_proxies:

    market_price_data = get_price_data(markets_proxies[market_name], '2002-08-04', '2025-04-04')
    market_variation_series = get_variation_series(market_price_data, '2002-08-04', '2025-04-04', 'weekly')

    market_data[market_name] = {
        'price_data': market_price_data,
        'variation_series': market_variation_series,
        'ticker': markets_proxies[market_name]
    }

'''
betas = {
    'company_ticker' : {
            'market_name': {
                'beta': beta,
                'intercept': intercept,
                'market_ticker': ticker
                
            }
    }
}
'''
betas = {}

for company_ticker in tickers_to_analize:

    company_data = get_price_data(company_ticker, '2002-08-04', '2025-04-04')
    company_variation_series = get_variation_series(company_data, '2002-08-04', '2025-04-04', 'weekly')

    markets = {}

    for market_name in market_data:

        market_variation_series = market_data[market_name]['variation_series']
        market_ticker = market_data[market_name]['ticker']

        # Calculate Beta
        beta, intercept = calc_beta(company_variation_series, market_variation_series)

        markets[market_name] = {
            'beta': beta,
            'intercept': intercept,
            'market_ticker': market_ticker,
        }

        
        betas[company_ticker] = markets

# print the betas dict into json format
#print(json.dumps(betas, indent=4))

#now, for every company, plotting results

for company_ticker in betas:

    # creating pd dataframe
    company_beta_data = betas[company_ticker]

    df = pd.DataFrame.from_dict(company_beta_data, orient='index')

    df = df.reset_index()
    df = df.rename(columns={'index': 'Market'})
    
    fig = px.bar(
        df,
        x='Market',          # Use the 'Market' column for the x-axis categories
        y='beta',            # Use the 'beta' column for the bar heights
        title=f'Beta of {company_ticker} Relative to Different Markets',
        labels={'beta': 'Beta Value', 'Market': 'Market Sector'},
        color='Market',      
        text='beta'          
    )

    fig.update_traces(texttemplate='%{text:.4f}', textposition='outside')
    # A beta of 1 means the stock moves with the market.
    fig.add_hline(y=1.0, line_dash="dash", line_color="red", annotation_text="Market Beta = 1.0")
    fig.write_image(f'results/beta_plots/{company_ticker}_beta.png')
    fig.show()



## 3.2 Portfolios Feasable and Efficient Frontiers

### 3.2.1 Defining the Core Functions

In [4]:
# to get one kind of risk of a portfolio: # bonds behave differently than stocks, the proce is the yield price
'''
ONE RISK comes from the volatility, that comes from a certain variation of the quantity of type of shares in the portfolio ( maybe variating markets )
this risk is associated with a earning

calculate avarge daily/weekly/montly/ early return of each asset in the portfolio
portfolio risk over the whole period of time
'''

#tying to het the oldest companys and markets

def get_earning_and_risk(portfolio: Portfolio, start_date, end_date, period_calculation='yearly', datapoints_period_calculation='weekly'):

    # calcualte mean anual earning of portfolio
    # calculate mean anual risk of the portfolio
    
    #getting mean_anual_risk:
    risk_series = portfolio.calculate_variating_portfolio_risk(start_date, end_date, period_calculation=period_calculation, datapoints_period_calculation=datapoints_period_calculation)
    mean_anual_risk = risk_series['Close'].mean()

    #getting mean_anual_earning:
    anual_series_earnings = portfolio.get_variating_portfolio_value(start_date,end_date, period_calculation=period_calculation)
    mean_anual_earning = anual_series_earnings['Variation'].mean()

    return (mean_anual_risk, mean_anual_earning)

def generate_systematic_weights(tickers: list, step: float = 0.05) -> list:
    """
    Generates all possible portfolio weight combinations that sum to 1.0,
    with the constraint that every weight must be at least the step size.

    This is a deterministic and exhaustive method: the number of
    combinations can grow very large very quickly.

    Args:
        tickers (list): A list of ticker symbols.
        step (float): The minimum percentage and step size for variation (e.g., 0.05 for 5%).

    Returns:
        list: A list of lists, where each inner list is a unique weight combination.
    """
    if not 0 < step <= 1.0:
        raise ValueError("Step size must be between 0 and 1.")

    #if 1.0 / step != round(1.0 / step):
     #   raise ValueError("1.0 must be perfectly divisible by the step size.")

    num_tickers = len(tickers)
    total_steps = int(round(1.0 / step))

    # Constraint check: The total number of steps must be at least the number of tickers,
    # since each ticker must get at least one step.
    if total_steps < num_tickers:
        print(f"Warning: Impossible to assign a minimum of {step*100}% to {num_tickers} tickers. Returning empty list.")
        return []

    # This is the recursive helper function that works with integers (steps).
    def find_combinations(n, total):
        # Base case: if we are assigning weight to the last ticker,
        # it must take all the remaining steps.
        if n == 1:
            yield [total]
            return

        # Recursive step: iterate through all possible values for the current ticker.
        for i in range(total + 1):
            for combo in find_combinations(n - 1, total - i):
                yield [i] + combo

    # We pre-assign one step to each ticker, so we have fewer steps to distribute.
    # The problem becomes: "Find all ways to add to the base allocation."
    steps_to_distribute = total_steps - num_tickers
    
    # Find all combinations for the remaining steps.
    # The original recursive function is perfect for this part.
    base_combinations = list(find_combinations(num_tickers, steps_to_distribute))
    
    # Convert integer step combinations back to float percentages
    all_weights = []
    for combo in base_combinations:
        # Add the 1 pre-assigned step back to each ticker's allocation,
        # then multiply by the step size to get the final percentage.
        weights = [round((i + 1) * step, 4) for i in combo]
        all_weights.append(weights)
        
    return all_weights

def process_single_portfolio(args):
    """
    Worker function that calculates risk/earning for a single set of weights.
    This is what each parallel process will execute.
    
    Args:
        args (tuple): A tuple containing all necessary arguments to avoid pickling issues with instance methods.
    
    Returns:
        dict: The data_pair dictionary for the calculated portfolio.
    """
    # 1. Unpack the arguments
    weights, tickers_list, start_date, end_date, tickers_to_account, \
    portfolio_initial_money, period_calculation, datapoints_period_calculation = args

    # 2. Create a NEW Portfolio object for each process
    # This is crucial as objects cannot be shared easily across processes.
    using_portfolio = Portfolio(id=1, money=portfolio_initial_money)
    
    # 3. Build the portfolio based on the weights

    try:
        for ticker, percentage in zip(tickers_list, weights):
            money_to_spend = portfolio_initial_money * percentage
            # Assuming buy_stock and tickers_to_account structure is correct
            using_portfolio.buy_stock(ticker, money_to_spend, start_date, tickers_to_account[ticker][0])
        
        # 4. Calculate the risk and earning
        risk, earning = get_earning_and_risk(
            using_portfolio, 
            start_date, 
            end_date, 
            period_calculation=period_calculation, 
            datapoints_period_calculation=datapoints_period_calculation
        )

        # 5. Assemble the result dictionary
        data_pair = {
            'risk': risk,
            'earning': earning,
            'tickers': [{'ticker': ticker, 'market': tickers_to_account[ticker][1], 'percentage': percentage} 
                        for ticker, percentage in zip(tickers_list, weights)]
        }
        
        return data_pair
    
    except Exception as e:
        return {
            'risk': None,
            'earning': None,
            'tickers': [{'ticker': ticker, 'market': tickers_to_account[ticker][1], 'percentage': percentage} 
                        for ticker, percentage in zip(tickers_list, weights)]
        }

def generate_risk_earnings_pairs_parallel(start_date, end_date, tickers_to_account, path_to_save_data, percentage_variation=0.05, period_calculation='yearly', datapoints_period_calculation='weekly', portfolio_initial_money=160000):
    # generate the Feasable Regeion of a Potfolio Configuration
    tickers_list = list(tickers_to_account.keys())
    # --- Weight Generation (same as before) ---
    limit = 1/percentage_variation
    if len(tickers_list) > limit:
        print(f"Warning: The number of tickers ({len(tickers_list)}) exceeds the limit ({limit}). Only the first {limit} tickers will be used.")
        tickers_list = tickers_list[:int(limit)]
    weights_distribution = generate_systematic_weights(tickers_list, step=percentage_variation)
    total_calc = len(weights_distribution)
    
    print(f"Generated {total_calc} weight combinations. Starting parallel processing...")
    

    # --- Parallel Execution ---
    # 1. Prepare the arguments for each worker call.
    #    We create a list of tuples, where each tuple contains all args for one call.
    tasks = [(
        weights, 
        tickers_list, 
        start_date, 
        end_date, 
        tickers_to_account,
        portfolio_initial_money, 
        period_calculation, 
        datapoints_period_calculation
    ) for weights in weights_distribution]

    # 2. Set up and run the pool of processes.
    #    'with Pool(...) as pool:' ensures the pool is properly closed.
    #    Using all available CPU cores for maximum speed.
    
    pairs = []
    print(f"Total calc: {total_calc}. This may take a while... {total_calc * 0.07} seconds max: {total_calc * 0.07 / 60} minutes, {total_calc * 0.07 / 3600} hours")
    with Pool(processes=cpu_count()) as pool:
        # pool.imap_unordered is an efficient iterator that returns results as they complete.
        # tqdm wraps this iterator to create a live progress bar.
        
        for result in pool.imap_unordered(process_single_portfolio, tasks):
            pairs.append(result)
    
    # --- Saving Results (same as before) ---

    print(f"\nProcessing complete. Saving {len(pairs)} results to {path_to_save_data}...")
    with open(path_to_save_data, 'w') as f:
        json.dump(pairs, f, indent=4)

    return pairs

def generate_risk_earnings_pairs(start_date, end_date, tickers_to_account, path_to_save_data, percentage_variation = 0.05, period_calculation='yearly', datapoints_period_calculation='weekly', portfolio_initial_money = 100000):
    pairs = []
    # for Speed Up computation i will use Multiprocessing
    '''
    pairs = [{
        risk: float,
        earning: float,
        tickers: [{
            ticker: str,
            market: str,
            percentage: float
        }
        ]
    
    }]
    '''
    using_portfolio = Portfolio(id=1, money=portfolio_initial_money)

    limit = 1/percentage_variation
    tickers_list = list(tickers_to_account.keys())

    if len(tickers_list) > limit:
        print(f"Warning: The number of tickers ({len(tickers_list)}) exceeds the limit ({limit}). Only the first {limit} tickers will be used.")
        tickers_list = tickers_list[:int(limit)]
    
    weights_distribution = generate_systematic_weights(tickers_list, step=percentage_variation)

    total_calc = len(weights_distribution)
    counter = 1

    # trying to use multiprocessing or threading for this part
    for weights in weights_distribution:
        ini_time = time.time()
        using_portfolio.reset()


        print(f"Calculating (risk, earning) for portfolio with weights: {weights}; \033[92m{counter/total_calc*100:.2f}% done\033[0m")

        for ticker, percentage in zip( tickers_list, weights):
            
            # Create a new portfolio for each weight combination
            
            money_to_spend = portfolio_initial_money * percentage
            
            # i will always have to reset the portfolio because there are some series calculated that would not change if i just changed the portfolio_percentages, 
            # resulting into wrong future calculations 
                

            using_portfolio.buy_stock(ticker, money_to_spend, start_date, tickers_to_account[ticker][0])
        
        # Calculate the risk and earning for the current portfolio
        risk, earning = get_earning_and_risk(using_portfolio, start_date, end_date, period_calculation=period_calculation, datapoints_period_calculation=datapoints_period_calculation)

        data_pair = {
            'risk': risk,
            'earning': earning,
            'tickers': [{'ticker': ticker, 'market': tickers_to_account[ticker][1], 'percentage': percentage} for ticker, percentage in zip(tickers_list, weights)]
        }

        pairs.append(data_pair)
        counter += 1

        print(f"\033[92m{counter/total_calc*100:.2f}% done, remaining {(time.time() - ini_time)*(total_calc - counter)} seconds\033[0m  \n")
    
    # save pairs as a json
    with open(path_to_save_data, 'w') as f:
        json.dump(pairs, f, indent=4)

    return pairs

def get_efficient_frontier(risk_earning_pairs, path):
    # path: path to append the perfect frontier data.
    risk_earning_df = pd.DataFrame(risk_earning_pairs)
    

    sorted = risk_earning_df.sort_values(by=['earning'], ascending=[False])
    sorted['min_risk_at_this_earning_or_higher'] = sorted['risk'].cummin()
    frontier_df = sorted[sorted['risk'] == sorted['min_risk_at_this_earning_or_higher']]

    with open(path, 'w') as f:
        json.dump(frontier_df.to_dict(orient='records'), f, indent=4)

    return frontier_df


### 3.2.1.1 Generating data

#### Testing

In [6]:
# testing:
tickers_to_acount_mixture = {
    '^TYX': ['bond', 'government', '30 year bond'],
    'XLE': ['ETF', 'energy', 'oil ETF'],
    'XLF': ['ETF', 'financials', 'financials ETF'],
    '^FTSE': ['index', 'international', 'UK 100'],
    '^STOXX50E': ['index', 'international', 'EURO STOXX 50'],
    'GC=F': ['Commodity', 'Gold', 'Gold Price'],
    'SNX': ['Crypto', 'Synthetix', 'Synthetix Network Token'],
    'AAPL': ['stock', 'information_technology', 'Apple Inc.'],
    'MSFT': ['stock', 'information_technology', 'Microsoft Corporation'],
    'IBM': ['stock', 'information_technology', 'International Business Machines Corporation'],

}

# market: energy, financials, automobilistic, agriculture, tecnology, government, 

tickers_to_account_by_market = {
    '^TYX': ['bond', 'government', '30 year bond'],
    '^SP500-15': ['Index', 'energy', 'energy indicators'],
    'XLF': ['ETF', 'financials', 'financials ETF'],
    '^RMZ': ['Index', 'real_estate', 'real estate ETF'],
    '^SP500-25': ['Index', 'Consumer', 'consumer_discretionary'],
    '^DJT': ['Index', 'transport', 'Transport ETF'],
    '^SP500-151040': ['Index', 'Metals', 'Metals and mining ETF'],
}



test_tickers = {
    'MSFT': ['stock', 'information_technology', 'Microsoft Corporation'],
    'GC=F': ['Commodity', 'Gold', 'Gold Price'],
    '^DJT': ['Index', 'transport', 'Transport ETF'],

}
if __name__ == '__main__':
    # --- Your setup code and function call would go here ---
    # For example:
    start = '2006-08-06'
    end = '2025-04-05'
    path = 'results/risk_earning_pairs/test4.json'
    #results = generate_risk_earnings_pairs_parallel(start, end, test_tickers, path, percentage_variation= 0.05)

In [54]:
results = generate_risk_earnings_pairs_parallel(start, end, test_tickers, path, percentage_variation= 0.01)

Generated 4851 weight combinations. Starting parallel processing...
Total calc: 4851. This may take a while... 339.57000000000005 seconds max: 5.6595 minutes, 0.09432500000000002 hours


/home/lucas-bussinger/.local/lib/python3.12/site-packages/pandas/core/nanops.py:1016: RuntimeWarning:

invalid value encountered in subtract

/home/lucas-bussinger/.local/lib/python3.12/site-packages/pandas/core/nanops.py:1016: RuntimeWarning:

invalid value encountered in subtract

/home/lucas-bussinger/.local/lib/python3.12/site-packages/pandas/core/nanops.py:1016: RuntimeWarning:

invalid value encountered in subtract

/home/lucas-bussinger/.local/lib/python3.12/site-packages/pandas/core/nanops.py:1016: RuntimeWarning:

invalid value encountered in subtract

/home/lucas-bussinger/.local/lib/python3.12/site-packages/pandas/core/nanops.py:1016: RuntimeWarning:

invalid value encountered in subtract

/home/lucas-bussinger/.local/lib/python3.12/site-packages/pandas/core/nanops.py:1016: RuntimeWarning:

invalid value encountered in subtract

/home/lucas-bussinger/.local/lib/python3.12/site-packages/pandas/core/nanops.py:1016: RuntimeWarning:

invalid value encountered in subtract

/home/


Processing complete. Saving 4851 results to results/risk_earning_pairs/test4.json...


### 3.2.2 Starting Simulation

#### First Portfolio Combinations

In [88]:

# getting the tickers i will use to analise
# bond, gold and apple
tk1 = {
    '^TYX': ['bond', 'government', '30 year bond'],
    'GC=F': ['Commodity', 'Gold', 'Gold Price'],
    'AAPL': ['stock', 'information_technology', 'Apple Inc.'], 
}

# microsoft, oil, energy
tk2 = {
    'MSFT': ['stock', 'information_technology', 'Microsoft Corporation'],
    'XOM': ['stock', 'oil', 'Stock price of ExxonMobil'],
    '^SP500-15': ['Index', 'energy', 'energy indicators'],
}
# real state, energy and apple
tk3 = {
    'WY': ['stock', 'real_estate', 'Weyerhaeuser Company'],
    '^SP500-15': ['Index', 'energy', 'energy indicators'],
    'AAPL': ['stock', 'information_technology', 'Apple Inc.'],
}

tk1_earning_risks = generate_risk_earnings_pairs_parallel('2004-04-06', '2025-02-06', tk1, f'results/risk_earning_pairs/{[ticker for ticker in tk1]}.json', percentage_variation=0.008)
tk2_earning_risks = generate_risk_earnings_pairs_parallel('2004-04-06', '2025-02-06', tk2, f'results/risk_earning_pairs/{[ticker for ticker in tk2]}.json', percentage_variation=0.008)
tk3_earning_risks = generate_risk_earnings_pairs_parallel('2004-04-06', '2025-02-06', tk3, f'results/risk_earning_pairs/{[ticker for ticker in tk3]}.json', percentage_variation=0.008)

Generated 7626 weight combinations. Starting parallel processing...
Total calc: 7626. This may take a while... 533.82 seconds max: 8.897 minutes, 0.14828333333333335 hours

Processing complete. Saving 7626 results to results/risk_earning_pairs/['^TYX', 'GC=F', 'AAPL'].json...
Generated 7626 weight combinations. Starting parallel processing...
Total calc: 7626. This may take a while... 533.82 seconds max: 8.897 minutes, 0.14828333333333335 hours

Processing complete. Saving 7626 results to results/risk_earning_pairs/['MSFT', 'XOM', '^SP500-15'].json...
Generated 7626 weight combinations. Starting parallel processing...
Total calc: 7626. This may take a while... 533.82 seconds max: 8.897 minutes, 0.14828333333333335 hours

Processing complete. Saving 7626 results to results/risk_earning_pairs/['WY', '^SP500-15', 'AAPL'].json...


In [89]:
tk1_risks = [pair['risk'] for pair in tk1_earning_risks]
tk1_earnings = [pair['earning'] for pair in tk1_earning_risks]

tk2_risks = [pair['risk'] for pair in tk2_earning_risks]
tk2_earnings = [pair['earning'] for pair in tk2_earning_risks]

tk3_risks = [pair['risk'] for pair in tk3_earning_risks]
tk3_earnings = [pair['earning'] for pair in tk3_earning_risks]

plot_scatter(tk1_risks, tk1_earnings, 'Risk', 'Earning', f'Risk vs Earning for {[ticker for ticker in tk1]}').show()
plot_scatter(tk2_risks, tk2_earnings, 'Risk', 'Earning', f'Risk vs Earning for {[ticker for ticker in tk2]}').show()
plot_scatter(tk3_risks, tk3_earnings, 'Risk', 'Earning', f'Risk vs Earning for {[ticker for ticker in tk3]}').show()

In [105]:
#Getting the frontiers:
tk1_frontier = get_efficient_frontier(tk1_earning_risks, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in tk1]}_frontier.json')
tk3_frontier = get_efficient_frontier(tk3_earning_risks, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in tk3]}_frontier.json')
tk2_frontier = get_efficient_frontier(tk2_earning_risks, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in tk2]}_frontier.json')


tk1_scat = px.scatter(x=tk1_frontier['risk'][0:1], y=tk1_frontier['earning'][0:1], title="Efficient Frontiers")
tk1_go = go.Scatter(x=tk1_frontier['risk'], y=tk1_frontier['earning'], mode='markers', marker = dict(color='blue', size = 4),name=f'{[ticker for ticker in tk1]} Frontier')
tk2_go = go.Scatter(x=tk2_frontier['risk'], y=tk2_frontier['earning'], mode='markers', marker = dict(color='red', size = 4),name=f'{[ticker for ticker in tk2]} Frontier')
tk3_go = go.Scatter(x=tk3_frontier['risk'], y=tk3_frontier['earning'], mode='markers', marker = dict(color='green', size = 4),name=f'{[ticker for ticker in tk3]} Frontier')

tk1_scat.add_trace(tk1_go)
tk1_scat.add_trace(tk2_go)
tk1_scat.add_trace(tk3_go)

tk1_scat.update_layout(xaxis_title='Risk (Expected)', yaxis_title='Earning (Expected)', legend_title='Portfolios Efficient Frontiers')


tk1_scat.write_image(f'results/portfolio_efficient_frontier_plots/{[ticker for ticker in list(tk1.keys()) + list(tk2.keys()) + list(tk3.keys())]}_frontier.jpg')
tk1_scat.show()

#### Second Portfolio Combinations

In [ ]:
# trying to get the "classic Curves" no bonds, just stocks
# Se p 500, bond, 
comparison_tk1 = {
    '^GSPC': ['stock', 'S&P 500 Index', 'S&P 500'],
    #'^TYX': ['bond', 'Total Bond Market', 'BND']
    'JPM': ['stock', 'financials', 'JPMorgan Chase & Co.']
}
comparison_tk1_add = {
    '^GSPC': ['stock', 'S&P 500 Index', 'S&P 500'],
    'JPM': ['stock', 'financials', 'JPMorgan Chase & Co.'],
    'ORCL': ['stock', 'comunications', 'Oracle Corporation']
}
comparison_tk1_add_2 = {
    '^GSPC': ['stock', 'S&P 500 Index', 'S&P 500'],
    'JPM': ['stock', 'financials', 'JPMorgan Chase & Co.'],
    'ORCL': ['stock', 'comunications', 'Oracle Corporation'],
    'MSFT': ['stock', 'information_technology', 'Microsoft Corporation'],
}
comparison_tk1_add_3 = {
    '^GSPC': ['stock', 'S&P 500 Index', 'S&P 500'],
    'JPM': ['stock', 'financials', 'JPMorgan Chase & Co.'],
    'ORCL': ['stock', 'comunications', 'Oracle Corporation'],
    'MSFT': ['stock', 'information_technology', 'Microsoft Corporation'],
    #'NFLX': ['stock', 'communications', 'Netflix, Inc.']
    'T': ['stock', 'communications', 'AT&T']
}
comparison_tk1_add_4 = {
    '^GSPC': ['stock', 'S&P 500 Index', 'S&P 500'],
    'JPM': ['stock', 'financials', 'JPMorgan Chase & Co.'],
    'ORCL': ['stock', 'comunications', 'Oracle Corporation'],
    'MSFT': ['stock', 'information_technology', 'Microsoft Corporation'],
    #'NFLX': ['stock', 'communications', 'Netflix, Inc.'],
    'T': ['stock', 'communications', 'AT&T'],
    'NKE': ['stock', 'consumer_discretionary', 'Nike, Inc.']
}



In [ ]:

comparison_risk_pairs_5 = generate_risk_earnings_pairs_parallel('2004-06-06', '2025-02-06', comparison_tk1_add_4, f'results/risk_earning_pairs/{[ticker for ticker in comparison_tk1_add_4]}.json', percentage_variation=0.045)
comparison_risk_pairs_4 = generate_risk_earnings_pairs_parallel('2004-06-06', '2025-02-06', comparison_tk1_add_3, f'results/risk_earning_pairs/{[ticker for ticker in comparison_tk1_add_3]}.json', percentage_variation=0.035)
comparison_risk_pairs_3 = generate_risk_earnings_pairs_parallel('2004-06-06', '2025-02-06', comparison_tk1_add_2, f'results/risk_earning_pairs/{[ticker for ticker in comparison_tk1_add_2]}.json', percentage_variation=0.023)
comparison_risk_pairs_1 = generate_risk_earnings_pairs_parallel('2004-06-06', '2025-02-06', comparison_tk1, f'results/risk_earning_pairs/{[ticker for ticker in comparison_tk1]}.json', percentage_variation=0.002)
comparison_risk_pairs_2 = generate_risk_earnings_pairs_parallel('2004-06-06', '2025-02-06', comparison_tk1_add, f'results/risk_earning_pairs/{[ticker for ticker in comparison_tk1_add]}.json', percentage_variation=0.008)



In [23]:
#plotting the feasable area
comparison_1_risks = [pair['risk'] for pair in comparison_risk_pairs_1]
comparison_1_earnings = [pair['earning'] for pair in comparison_risk_pairs_1]

comparison_2_risks = [pair['risk'] for pair in comparison_risk_pairs_2]
comparison_2_earnings = [pair['earning'] for pair in comparison_risk_pairs_2]

comparison_3_risks = [pair['risk'] for pair in comparison_risk_pairs_3]
comparison_3_earnings = [pair['earning'] for pair in comparison_risk_pairs_3]

comparison_4_risks = [pair['risk'] for pair in comparison_risk_pairs_4]
comparison_4_earnings = [pair['earning'] for pair in comparison_risk_pairs_4]

comparison_5_risks = [pair['risk'] for pair in comparison_risk_pairs_5]
comparison_5_earnings = [pair['earning'] for pair in comparison_risk_pairs_5]

plot_comparison_1 = px.scatter(x=comparison_1_risks, y=comparison_1_earnings, title=f"Risks vs Earnings for {[ticker for ticker in comparison_tk1]}")
plot_comparison_2 = px.scatter(x=comparison_2_risks, y=comparison_2_earnings, title=f"Risks vs Earnings for {[ticker for ticker in comparison_tk1_add]}")
plot_comparison_3 = px.scatter(x=comparison_3_risks, y=comparison_3_earnings, title=f"Risks vs Earnings for {[ticker for ticker in comparison_tk1_add_2]}")
plot_comparison_4 = px.scatter(x=comparison_4_risks, y=comparison_4_earnings, title=f"Risks vs Earnings for {[ticker for ticker in comparison_tk1_add_3]}")
plot_comparison_5 = px.scatter(x=comparison_5_risks, y=comparison_5_earnings, title=f"Risks vs Earnings for {[ticker for ticker in comparison_tk1_add_4]}")

plot_comparison_1.update_layout(xaxis_title='Risk', yaxis_title='Earning')
plot_comparison_2.update_layout(xaxis_title='Risk', yaxis_title='Earning')
plot_comparison_3.update_layout(xaxis_title='Risk', yaxis_title='Earning')
plot_comparison_4.update_layout(xaxis_title='Risk', yaxis_title='Earning')
plot_comparison_5.update_layout(xaxis_title='Risk', yaxis_title='Earning')

plot_comparison_1.write_image(f'results/portfolio_frontier_plots/{[ticker for ticker in comparison_tk1]}_comparison.jpg')
plot_comparison_2.write_image(f'results/portfolio_frontier_plots/{[ticker for ticker in comparison_tk1_add]}_comparison.jpg')
plot_comparison_3.write_image(f'results/portfolio_frontier_plots/{[ticker for ticker in comparison_tk1_add_2]}_comparison.jpg')
plot_comparison_4.write_image(f'results/portfolio_frontier_plots/{[ticker for ticker in comparison_tk1_add_3]}_comparison.jpg')
plot_comparison_5.write_image(f'results/portfolio_frontier_plots/{[ticker for ticker in comparison_tk1_add_4]}_comparison.jpg')

plot_comparison_1.show()
plot_comparison_2.show()
plot_comparison_3.show()
plot_comparison_4.show()
plot_comparison_5.show()

In [24]:
comparison_1_efficient = get_efficient_frontier(comparison_risk_pairs_1, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in comparison_tk1]}_frontier.json')
comparison_2_efficient = get_efficient_frontier(comparison_risk_pairs_2, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in comparison_tk1_add]}_frontier.json')
comparison_3_efficient = get_efficient_frontier(comparison_risk_pairs_3, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in comparison_tk1_add_2]}_frontier.json')
comparison_4_efficient = get_efficient_frontier(comparison_risk_pairs_4, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in comparison_tk1_add_3]}_frontier.json')
comparison_5_efficient = get_efficient_frontier(comparison_risk_pairs_5, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in comparison_tk1_add_4]}_frontier.json')

comp_1_risks = comparison_1_efficient['risk']
comp_1_earnings = comparison_1_efficient['earning']

comp_2_risks = comparison_2_efficient['risk']
comp_2_earnings = comparison_2_efficient['earning']

comp_3_risks = comparison_3_efficient['risk']
comp_3_earnings = comparison_3_efficient['earning']

comp_4_risks = comparison_4_efficient['risk']
comp_4_earnings = comparison_4_efficient['earning']

comp_5_risks = comparison_5_efficient['risk']
comp_5_earnings = comparison_5_efficient['earning']

comp_plot = px.scatter(title="Efficient Frontiers Comparison")
comp_plot.add_scatter(x=comp_1_risks, y=comp_1_earnings, mode='markers', marker=dict(color='blue', size = 4), name=f'{[ticker for ticker in comparison_tk1]}')
comp_plot.add_scatter(x=comp_2_risks, y=comp_2_earnings, mode='markers', marker=dict(color='red', size = 4), name=f'{[ticker for ticker in comparison_tk1_add]}')
comp_plot.add_scatter(x=comp_3_risks, y=comp_3_earnings, mode='markers', marker=dict(color='green', size = 4), name=f'{[ticker for ticker in comparison_tk1_add_2]}')
comp_plot.add_scatter(x=comp_4_risks, y=comp_4_earnings, mode='markers', marker=dict(color='orange', size = 4), name=f'{[ticker for ticker in comparison_tk1_add_3]}')
comp_plot.add_scatter(x=comp_5_risks, y=comp_5_earnings, mode='markers', marker=dict(color='purple', size = 4), name=f'{[ticker for ticker in comparison_tk1_add_4]}')

comp_plot.update_layout(xaxis_title='Risk (Expected)', yaxis_title='Earning (Expected)', legend_title='Portfolios Efficient Frontiers Comparison')

comp_plot.write_image(f'results/portfolio_efficient_frontier_plots/{[ticker for ticker in comparison_tk1_add_4]}_comparison.jpg')
comp_plot.show()

In [15]:
# Calculating with completly different tickers ( sets of 3):
#real_estate, information_technology, financials
tk1 = {
    'ESS': ['stock', 'real_estate', 'Essex Property Trust, Inc.'],
    'ORCL': ['stock', 'information_technology', 'Oracle Corporation'],
    'BAC': ['stock', 'financials', 'Bank of America Corporation']
}

# microsoft, oil, energy
tk2 = {
    'MSFT': ['stock', 'information_technology', 'Microsoft Corporation'],
    'XOM': ['stock', 'oil', 'Stock price of ExxonMobil'],
    '^SP500-15': ['Index', 'energy', 'energy indicators'],
}

#communications, health_care, consumer_discretionary
tk3 = {
    #'NFLX': ['stock', 'communications', 'Netflix, Inc.'],
    'TTWO': ['stock', 'communications', 'Take-Two Interactive Software, Inc.'],
    'UNH': ['stock', 'health_care', 'UnitedHealth Group Incorporated'],
    'EBAY': ['stock', 'consumer_discretionary', 'eBay Inc.']
}


In [16]:

#Calculating:

tk1_risk_earning_pairs = generate_risk_earnings_pairs_parallel('2004-04-06', '2025-02-06', tk1, f'results/risk_earning_pairs/{[ticker for ticker in tk1]}.json', percentage_variation=0.01)
tk2_risk_earning_pairs = generate_risk_earnings_pairs_parallel('2004-04-06', '2025-02-06', tk2, f'results/risk_earning_pairs/{[ticker for ticker in tk2]}.json', percentage_variation=0.01)
tk3_risk_earning_pairs = generate_risk_earnings_pairs_parallel('2004-04-06', '2025-02-06', tk3, f'results/risk_earning_pairs/{[ticker for ticker in tk3]}.json', percentage_variation=0.01)


Generated 4851 weight combinations. Starting parallel processing...
Total calc: 4851. This may take a while... 339.57000000000005 seconds max: 5.6595 minutes, 0.09432500000000002 hours

Processing complete. Saving 4851 results to results/risk_earning_pairs/['ESS', 'ORCL', 'BAC'].json...
Generated 4851 weight combinations. Starting parallel processing...
Total calc: 4851. This may take a while... 339.57000000000005 seconds max: 5.6595 minutes, 0.09432500000000002 hours

Processing complete. Saving 4851 results to results/risk_earning_pairs/['MSFT', 'XOM', '^SP500-15'].json...
Generated 4851 weight combinations. Starting parallel processing...
Total calc: 4851. This may take a while... 339.57000000000005 seconds max: 5.6595 minutes, 0.09432500000000002 hours

Processing complete. Saving 4851 results to results/risk_earning_pairs/['TTWO', 'UNH', 'EBAY'].json...


In [17]:
# Plotting the feasable areas

tk1_risks = [pair['risk'] for pair in tk1_risk_earning_pairs]
tk1_earnings = [pair['earning'] for pair in tk1_risk_earning_pairs]

tk2_risks = [pair['risk'] for pair in tk2_risk_earning_pairs]
tk2_earnings = [pair['earning'] for pair in tk2_risk_earning_pairs]

tk3_risks = [pair['risk'] for pair in tk3_risk_earning_pairs]
tk3_earnings = [pair['earning'] for pair in tk3_risk_earning_pairs]

plot = px.scatter(title="Feasable areas")
plot.add_scatter(x=tk1_risks, y=tk1_earnings, mode='markers', marker=dict(color='blue', size=4), name=f'{[ticker for ticker in tk1]}')
plot.add_scatter(x=tk2_risks, y=tk2_earnings, mode='markers', marker=dict(color='red', size=4), name=f'{[ticker for ticker in tk2]}')
plot.add_scatter(x=tk3_risks, y=tk3_earnings, mode='markers', marker=dict(color='green', size=4), name=f'{[ticker for ticker in tk3]}')

plot.update_layout(xaxis_title="Risk ( Expected )", yaxis_title="Earnings ( Expected )")

plot.write_image(f'results/portfolio_frontier_plots/{[ticker for ticker in tk1] + [ticker for ticker in tk2] + [ticker for ticker in tk3]}_comparison.jpg')
plot.show()


In [18]:
#Getting Efficient_frontiers

tk1_efficient = get_efficient_frontier(tk1_risk_earning_pairs, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in tk1]}_frontier.json')
tk2_efficient = get_efficient_frontier(tk2_risk_earning_pairs, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in tk2]}_frontier.json')
tk3_efficient = get_efficient_frontier(tk3_risk_earning_pairs, f'results/risk_earning_efficient_frontiers/{[ticker for ticker in tk3]}_frontier.json')

tk1_comp_risks = tk1_efficient['risk']
tk1_comp_earnings = tk1_efficient['earning']

tk2_comp_risks = tk2_efficient['risk']
tk2_comp_earnings = tk2_efficient['earning']

tk3_comp_risks = tk3_efficient['risk']
tk3_comp_earnings = tk3_efficient['earning']

#generating plot

plt_comparison = px.scatter(title="Efficient Frontiers")
plt_comparison.add_scatter(x=tk1_comp_risks, y=tk1_comp_earnings, mode='markers', marker=dict(color='blue', size=4), name=f'{[ticker for ticker in tk1]}')
plt_comparison.add_scatter(x=tk2_comp_risks, y=tk2_comp_earnings, mode='markers', marker=dict(color='red', size=4), name=f'{[ticker for ticker in tk2]}')
plt_comparison.add_scatter(x=tk3_comp_risks, y=tk3_comp_earnings, mode='markers', marker=dict(color='green', size=4), name=f'{[ticker for ticker in tk3]}')

plt_comparison.update_layout(xaxis_title='Risk (Expected)', yaxis_title='Earning (Expected)', legend_title='Portfolios Efficient Frontiers Comparison')

plt_comparison.write_image(f'results/portfolio_efficient_frontier_plots/{[ticker for ticker in tk1] + [ticker for ticker in tk2] + [ticker for ticker in tk3]}_frontier.jpg')
plt_comparison.show()


## 3.3 Sharpe Ratios of Efficient Portfolios

In [4]:
# getting data from efficient frontiers
# mounting the portfolio with the perfect combinations
# calculating sharpe_ratios
sharpe_ratio_calculator = Sharpe_Ratio_Calculator()
# going to use data from 

data_batch_1 = [
    ['^GSPC', 'JPM'],
    ['^GSPC', 'JPM', 'ORCL'],
    ['^GSPC', 'JPM', 'ORCL', 'MSFT'],
    ['^GSPC', 'JPM', 'ORCL', 'MSFT', 'NFLX'],
]
data_batch_2 = [
    ['^GSPC', 'JPM'],
    ['^GSPC', 'JPM', 'ORCL'],
    ['^GSPC', 'JPM', 'ORCL', 'MSFT'],
    ['^GSPC', 'JPM', 'ORCL', 'MSFT', 'T'],
    ['^GSPC', 'JPM', 'ORCL', 'MSFT', 'T', 'NKE'],
]
data_batch_3 = [
    ['ESS', 'ORCL', 'BAC'],
    ['MSFT', 'XOM', '^SP500-15'],
    ['TTWO', 'UNH', 'EBAY'],
]

all_batches = [data_batch_1, data_batch_2, data_batch_3]

# i will only get the "less risk, less reward" and "most, risk, most reward" percentages datapoints of each batch conjunct
# getting the percentages datapoints
batch_1_data = {}
batch_2_data = {}
batch_3_data = {}

all_batches_data = [batch_1_data, batch_2_data, batch_3_data]

counter = 0


''' 
sharpe_ratios_dict = {
    [TTWO, GSPC]: {
        min_risk : sharpe Ratio
        max_risk : sharpe Ratio
        mean_risk : sharpe Ratio
    }
}


'''
sharpe_ratios_dict = {}

for batch in all_batches:

    for tickers_list in batch:
        # load a josn with pd dataframe
        tickers_list_df = pd.read_json(f'results/risk_earning_efficient_frontiers/{tickers_list}_frontier.json')
        
        # getting the less risk, less reward percentages
        
        min_risk_data = tickers_list_df.loc[tickers_list_df['risk'] == tickers_list_df['risk'].min()]['tickers']
        
        # getting most risk, most reward percentages
        max_risk_data = tickers_list_df.loc[tickers_list_df['risk'] == tickers_list_df['risk'].max()]['tickers']

        min_risk_data = min_risk_data[min_risk_data.index[0]]
        max_risk_data = max_risk_data[max_risk_data.index[0]]

        # get the midle: mean risk and mean earning
        abs_diff = (tickers_list_df['risk'] - tickers_list_df['risk'].mean()).abs()
        closest_index = abs_diff.idxmin()

        mean_risk_data = tickers_list_df.loc[closest_index, 'tickers']
    
        all_batches_data[counter][str(tickers_list)] = {
            'min_risk' : min_risk_data,
            'max_risk' : max_risk_data,
            'mean_risk' : mean_risk_data,
            'tickers': tickers_list
        }
        risks_list_data = [min_risk_data, mean_risk_data, max_risk_data]

        #mounting portfolio

        
        counter2 = 0
        for risk_data_list in risks_list_data:

            if counter2 == 0:
                risk_type = "min_risk"
            elif counter2 == 1:
                risk_type = "mean_risk"
            elif counter2 == 2:
                risk_type = "max_risk"
            else:
                risk_type = None

            testing_portfolio = Portfolio(id=1, money=160000)

            #buying the tickers with percentages
            for ticker_info_dict in risk_data_list:
                testing_portfolio.buy_stock(ticker_info_dict['ticker'], ticker_info_dict['percentage']*testing_portfolio.initial_money, '2002-08-04', 'stock')
            
            # calculating the sharpe ratio for portfolio
            portfolio_var_series = testing_portfolio.calculate_variating_portfolio_value('2002-08-04', '2025-04-04')
            portfolio_var_series.replace([np.inf, -np.inf], 0, inplace=True)

            current_sharpe_ratio = sharpe_ratio_calculator.calculate(portfolio_var_series, '2002-08-04', '2025-04-04')


            if str(tickers_list) not in sharpe_ratios_dict:
                sharpe_ratios_dict[str(tickers_list)] = {}
            
            sharpe_ratios_dict[str(tickers_list)][risk_type] = current_sharpe_ratio

            counter2 += 1


    counter += 1

print(sharpe_ratios_dict)

{"['^GSPC', 'JPM']": {'min_risk': 0.4616725877945997, 'mean_risk': 0.49268419762226223, 'max_risk': 0.4921838221500284}, "['^GSPC', 'JPM', 'ORCL']": {'min_risk': 0.4675197508796455, 'mean_risk': 0.5641458654888906, 'max_risk': 0.5459120365323403}, "['^GSPC', 'JPM', 'ORCL', 'MSFT']": {'min_risk': 0.49572019235854214, 'mean_risk': 0.6605970688570942, 'max_risk': 0.6528250181706694}, "['^GSPC', 'JPM', 'ORCL', 'MSFT', 'NFLX']": {'min_risk': 0.704819133355811, 'mean_risk': 0.7711032402865522, 'max_risk': 0.8046038019063708}, "['^GSPC', 'JPM', 'ORCL', 'MSFT', 'T']": {'min_risk': 0.5273198448935379, 'mean_risk': 0.6755128939198242, 'max_risk': 0.6603299366023472}, "['^GSPC', 'JPM', 'ORCL', 'MSFT', 'T', 'NKE']": {'min_risk': 0.5475693111897871, 'mean_risk': 0.6773534026317275, 'max_risk': 0.6767993901618138}, "['ESS', 'ORCL', 'BAC']": {'min_risk': 0.543454550747105, 'mean_risk': 0.5863473070386329, 'max_risk': 0.5458596689492377}, "['MSFT', 'XOM', '^SP500-15']": {'min_risk': 0.5509629825697439

In [5]:
#Plotting Findings
print(sharpe_ratios_dict)

full_df = pd.DataFrame.from_dict(sharpe_ratios_dict, orient='index')
# Reset the index to make the portfolio strings a regular column
full_df = full_df.reset_index()
full_df = full_df.rename(columns={'index': 'Portfolio'})


risk_types = ['min_risk', 'mean_risk', 'max_risk']

for risk_type in risk_types:
    

    df_to_plot = full_df
    

    print(f"\n--- Generating plot for {risk_type} ---")
    fig = px.bar(
        df_to_plot,
        x='Portfolio',       
        y=risk_type,         
        title=f"Sharpe Ratios for Portfolio's Efficient Frontiers in {risk_type}/earning configuration",
        labels={risk_type: 'Sharpe Ratio', 'Portfolio': 'Portfolio Composition'},
        color='Portfolio',     
        text=risk_type       
    )

    fig.update_traces(texttemplate='%{text:.4f}', textposition='outside')
    

    fig.update_layout(xaxis_tickangle=-45)
    

    fig.add_hline(
        y=1.0, 
        line_dash="dash", 
        line_color="red", 
        annotation_text="Sharpe Ratio = 1.0 (VERY Good Risk-Adjusted Return)", 
        annotation_position="bottom right"
    )
    
    
    fig.show()
    fig.write_image(f'results/portfolio_efficient_sharpe_ratios_plots/sharpe_ratios_{risk_type}.png')


{"['^GSPC', 'JPM']": {'min_risk': 0.4616725877945997, 'mean_risk': 0.49268419762226223, 'max_risk': 0.4921838221500284}, "['^GSPC', 'JPM', 'ORCL']": {'min_risk': 0.4675197508796455, 'mean_risk': 0.5641458654888906, 'max_risk': 0.5459120365323403}, "['^GSPC', 'JPM', 'ORCL', 'MSFT']": {'min_risk': 0.49572019235854214, 'mean_risk': 0.6605970688570942, 'max_risk': 0.6528250181706694}, "['^GSPC', 'JPM', 'ORCL', 'MSFT', 'NFLX']": {'min_risk': 0.704819133355811, 'mean_risk': 0.7711032402865522, 'max_risk': 0.8046038019063708}, "['^GSPC', 'JPM', 'ORCL', 'MSFT', 'T']": {'min_risk': 0.5273198448935379, 'mean_risk': 0.6755128939198242, 'max_risk': 0.6603299366023472}, "['^GSPC', 'JPM', 'ORCL', 'MSFT', 'T', 'NKE']": {'min_risk': 0.5475693111897871, 'mean_risk': 0.6773534026317275, 'max_risk': 0.6767993901618138}, "['ESS', 'ORCL', 'BAC']": {'min_risk': 0.543454550747105, 'mean_risk': 0.5863473070386329, 'max_risk': 0.5458596689492377}, "['MSFT', 'XOM', '^SP500-15']": {'min_risk': 0.5509629825697439


--- Generating plot for mean_risk ---



--- Generating plot for max_risk ---
